In [2]:
from numpy import array
import tensorflow as tf
import glob
import numpy as np
import pickle

from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.utils import to_categorical
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.models import Sequential,Model
from tensorflow.keras.layers import Dense
from tensorflow.keras.layers import LSTM
from tensorflow.keras.layers import Input
from tensorflow.keras.layers import Dropout
from tensorflow.keras.layers import Embedding
from tensorflow.keras.layers import TimeDistributed
from tensorflow.keras.layers import Conv1D
from tensorflow.keras.layers import LSTM,Bidirectional,MaxPooling1D,Flatten,concatenate
from tensorflow.keras.utils import Progbar
from tensorflow.keras.models import load_model

from tensorflow.keras.initializers import RandomUniform


In [41]:
class LoadData():
    def __init__(self):
        self.train_files = None
        self.validation_files = None
        
    def get_data(self):
        self.train_files = glob.glob("benchmarking_data/Train//*.txt")
        self.validation_files = glob.glob("benchmarking_data/Validate//*.txt")
        
    def sentence_from_file(self,filename):
        f = open(filename)
        single_file_sentences = []
        sentence_list = []
        for line in f:
            print(line)
            try:
                splits = line.split(' ')
                if len(splits)==3:
                    sentence_list.append((splits[0],splits[1],splits[-1].replace('\n','')))
            except Exception as e:
                print(e)
                pass
        return sentence_list
    
    def addCharInformatioin(self,Sentences):
        for i,sentence in enumerate(Sentences):
            for j,data in enumerate(sentence):
                chars = [c for c in data[0]]
                Sentences[i][j] = [data[0],chars,data[1],data[2]]
        return Sentences
    
    def prepared_data(self,files):
        list_sentences = []
        for each_file in files:
            sentences = self.sentence_from_file(each_file)
            #sentences = self.addCharInformatioin(sentences)
            list_sentences+= sentences
        return list_sentences
    

In [42]:
load_data_obj = LoadData()
load_data_obj.get_data()
trained_sen_list = load_data_obj.prepared_data(load_data_obj.train_files)
validation_sen_list = load_data_obj.prepared_data(load_data_obj.validation_files)
print(trained_sen_list[:5])

book NN O

The DT B-restaurant_name

Middle NNP I-restaurant_name

East NNP I-restaurant_name

restaurant NN B-restaurant_type

in IN O

IN NNP B-state

for IN O

noon NN B-timeRange



Book VB O

a DT O

table NN O

at IN O

T-Rex NNP B-restaurant_name

distant NN B-spatial_relation

from IN O

Halsey NNP B-poi

St NNP I-poi

. . O



I'd NNP O

like IN O

to TO O

eat VB O

at IN O

a DT O

taverna NN B-restaurant_type

that WDT O

serves VBZ O

chili JJ B-served_dish

con NN I-served_dish

carne NN I-served_dish

for IN O

a DT O

party NN O

of IN O

10 CD B-party_size_number



I PRP O

have VBP O

a DT O

party NN O

of IN O

four CD B-party_size_number

in IN O

Japan NNP B-country

and CC O

need VBP O

a DT O

reservation NN O

at IN O

Rimsky-Korsakoffee NNP B-restaurant_name

House NNP I-restaurant_name

on IN O

Aug. NNP B-timeRange

the DT I-timeRange

3rd CD I-timeRange

. . O



Please NNP O

make VB O

a DT O

restaurant NN B-restaurant_type

reservation NN O

for IN O


oyster NN B-restaurant_type

bar NN I-restaurant_type

for IN O

five CD B-party_size_number

people. NNS O



Give VB O

me PRP O

a DT O

top-rated JJ B-sort

restaurant NN B-restaurant_type

that's NN O

eastern JJ B-cuisine

european JJ I-cuisine



book NN O

a DT O

tea NN B-restaurant_type

house NN I-restaurant_type

on IN O

5/20/2028 CD B-timeRange

in IN O

Pataskala NNP B-city

that WDT O

serves VBZ O

crepe NN B-served_dish

in IN O

NC NNP B-state

for IN O

five CD B-party_size_number



book NN O

a DT O

spot NN O

for IN O

1 CD B-party_size_number

close JJ B-spatial_relation

to TO O

geraldine's VB B-poi

house NN I-poi



I PRP O

want VBP O

to TO O

eat VB O

breakfast NN B-timeRange

at IN O

the DT O

Green NNP B-restaurant_name

Restaurant NNP I-restaurant_name

Certification NNP I-restaurant_name



I PRP O

want VBP O

to TO O

book NN O

a DT O

restaurant NN B-restaurant_type

in IN O

Wallsburg NNP B-city

, , O

Missouri NNP B-state

for IN O

michele,


six CD B-party_size_number

people NNS O



book NN O

a DT O

table NN O

for IN O

7 CD B-party_size_number

at IN O

a DT O

churrascaria NN B-restaurant_type

that WDT O

is VBZ O

highly RB B-sort

rated VBN I-sort



Take VB O

me PRP O

to TO O

the DT O

top-rated JJ B-sort

taverna NN B-restaurant_type

in IN O

Sealy NNP B-city

for IN O

trattoria NNS B-cuisine

next JJ B-timeRange

week NN I-timeRange

for IN O

5 CD B-party_size_number



I PRP O

need VBP O

a DT O

reservation NN O

for IN O

me, NN B-party_size_description

edna NN I-party_size_description

and CC I-party_size_description

alyson NN I-party_size_description

at IN O

the DT O

steakhouse NN B-restaurant_type

called VBD O

smoking NN B-facility

room NN I-facility



susanne NN B-party_size_description

and CC I-party_size_description

carey JJ I-party_size_description

phillips NNS I-party_size_description

want VBP O

to TO O

go VB O

to TO O

a DT O

brasserie NN B-restaurant_type

not RB B-spatial


Reserve NNP O

a DT O

table NN O

for IN O

8 CD B-party_size_number

in IN O

neighboring VBG B-spatial_relation

Hitchland NNP B-city

. . O



I PRP O

want VBP O

to TO O

book NN O

a DT O

highly RB B-sort

rated VBN I-sort

fast RB B-restaurant_type

food NN I-restaurant_type

restaurant NN I-restaurant_type

now RB B-timeRange

. . O



Find IN O

a DT O

table NN O

somewhere RB O

for IN O

me PRP B-party_size_description

and CC I-party_size_description

my PRP$ I-party_size_description

step NN I-party_size_description

mother RB I-party_size_description

in IN O

Graniteville NNP B-city

DE NNP B-state



Please NNP O

reserve VB O

a DT O

spot NN O

at IN O

Ballachulish NNP B-restaurant_name

House NNP I-restaurant_name

. . O



I PRP O

would MD O

like VB O

an DT O

outdoor JJ B-facility

cafeteria NN B-restaurant_type

for IN O

3 CD B-party_size_number



book NN O

a DT O

table NN O

for IN O

ten JJ B-party_size_number

people NNS O

at IN O

a DT O

restaura

I'd NNP O

like IN O

to TO O

eat VB O

at IN O

a DT O

top-rated JJ B-sort

place NN O

on IN O

nov. IN B-timeRange

the DT I-timeRange

twenty-sixth JJ I-timeRange

in IN O

the DT O

food NN B-restaurant_type

court NN I-restaurant_type

, , O

I PRP O

need VBP O

reservations NNS O

for IN O

7 CD B-party_size_number

in IN O

the DT O

city NN O

of IN O

Kane NNP B-city

or CC O

somewhere RB O

near IN B-spatial_relation

there. NN O



Book NNP O

me PRP O

a DT O

table NN O

for IN O

seven CD B-party_size_number

in IN O

neighboring VBG B-spatial_relation

France NNP B-country

. . O



book NN O

in IN O

Falkland NNP B-country

Islands NNP I-country

at IN O

Atomic NNP B-restaurant_name

Cafe NNP I-restaurant_name



I PRP O

want VBP O

to TO O

take VB O

four CD B-party_size_number

friends NNS O

to TO O

the DT O

pub NN B-restaurant_type

for IN O

some DT O

tuna NN B-served_dish

casserole NN I-served_dish



I PRP O

need VBP O

a DT O

reservation NN O

in 

...


van NN I-artist

Leeuwen NNP I-artist

to TO O

my PRP$ B-playlist_owner

nu JJ B-playlist

metal JJ I-playlist

list NN O



Add IN O

the DT O

singer JJR O

Maxine NNP B-artist

Nightingale NNP I-artist

to TO O

the DT O

Spanish JJ B-playlist

Beat NNP I-playlist

playlist. NN O



add VB O

Tarte NNP B-entity_name

to TO O

bandas VB B-playlist

sonoras NNS I-playlist

playlist VB O



add VB O

jeff NN B-artist

burrows NNS I-artist

album VBP B-music_item

to TO O

my PRP$ B-playlist_owner

Country NNP B-playlist

Hits NNP I-playlist

playlist NN O



add VB O

this DT O

tune NN B-music_item

to TO O

my PRP$ B-playlist_owner

Rock NNP B-playlist

This DT I-playlist



Add NNP O

impossible JJ B-entity_name

is VBZ I-entity_name

nothing NN I-entity_name

to TO O

SPA NNP B-playlist

Treatment NNP I-playlist



Add VB O

a DT O

tune NN B-music_item

to TO O

Skylar NNP B-playlist

Diggins' NNP I-playlist

Training NNP I-playlist

Mix NNP I-playlist



Add VB O

a DT O

track


activity NN I-playlist

playlist NN O

add IN O

the DT O

name NN O

The DT B-entity_name

Best NNP I-entity_name

of IN I-entity_name

Guitar NNP I-entity_name

Shorty NNP I-entity_name



Can MD O

you PRP O

add VB O

something NN O

by IN O

Faultline NNP B-artist

to TO O

jannie's VB B-playlist_owner

Strength NNP B-playlist

of IN I-playlist

Street NNP I-playlist

Knowledge NNP I-playlist

playlist NN O



Add VB O

this DT O

song NN B-music_item

to TO O

my PRP$ B-playlist_owner

lo NN B-playlist

que NN I-playlist

suena VBD I-playlist

new JJ I-playlist

york NN I-playlist

playlist NN O



matt NN B-artist

monro NN I-artist

newest JJS O

album NN B-music_item

add NN O

to TO O

my PRP$ B-playlist_owner

chill NN B-playlist

out RP I-playlist

music NN I-playlist



add VB O

house NN B-playlist

afterwork NN I-playlist

to TO O

my PRP$ B-playlist_owner

the DT B-entity_name

cave NN I-entity_name

canem NN I-entity_name

demos NN I-entity_name



put VB O

Johnny NN


playlist NN O

kitchen NN B-playlist

swagger NN I-playlist



add VB O

this DT O

elbridge NN B-artist

bryant NN I-artist

song NN B-music_item

to TO O

my PRP$ B-playlist_owner

inyeccion NN B-playlist

musical JJ I-playlist

playlist NN O



In IN O

my PRP$ B-playlist_owner

playlist NN O

Rock NNP B-playlist

Gaming NNP I-playlist

add VB O

Mariem NNP B-entity_name

Hassan NNP I-entity_name

con NN I-entity_name

Leyoad NNP I-entity_name



Add IN O

the DT O

singer NN O

Damon NNP B-artist

Johnson NNP I-artist

album NN B-music_item

to TO O

my PRP$ B-playlist_owner

African JJ B-playlist

Heat NNP I-playlist

playlists NNS O



Can MD O

you PRP O

put VB O

consequences NNS B-entity_name

on IN O

my PRP$ B-playlist_owner

SOS CD B-playlist

48 CD I-playlist

2016 CD I-playlist

playlist NN O



will MD O

you PRP O

add VB O

Pat NNP B-artist

Kirtley NNP I-artist

to TO O

my PRP$ B-playlist_owner

covered VBN B-playlist

in IN I-playlist

punk NN I-playlist

playlist


1 CD B-rating_value

star NN O



mark NN O

this DT B-object_select

album VBZ B-object_type

a DT O

score NN O

of IN O

5 CD B-rating_value



rate NN O

the DT O

current JJ B-object_select

novel NN B-object_type

zero CD B-rating_value

out IN O

of IN O

6 CD B-best_rating



rate NN O

the DT O

current JJ B-object_select

novel NN B-object_type

a DT O

2 CD B-rating_value



Give VB O

The DT B-object_name

Giant NNP I-object_name

Devil NNP I-object_name

Dingo NNP I-object_name

4 CD B-rating_value

points NNS B-rating_unit

. . O



Rate VB O

this DT B-object_select

current JJ I-object_select

novel NN B-object_type

two CD B-rating_value

out IN O

of IN O

6 CD B-best_rating

. . O



Give VB O

Monthly NNP B-object_name

Index NNP I-object_name

of IN I-object_name

Medical NNP I-object_name

Specialities NNP I-object_name

a DT O

two CD B-rating_value

out IN O

of IN O

6 CD B-best_rating

rating. NN O



rate NN O

this DT B-object_select

novel $ B-object_type



AMT NNP B-restaurant_name

Coffee NNP I-restaurant_name

in IN O

Lakemoor NNP B-city



I PRP O

want VBP O

to TO O

book NN O

a DT O

churrascaria NN B-restaurant_type

in IN O

Romeoville NNP B-city

at IN O

ten JJ B-timeRange

a.m NN I-timeRange

for IN O

four CD B-party_size_number

people. NN O



table NN O

for IN O

5 CD B-timeRange

A.m NNP I-timeRange

. . O

at IN O

Baker's NNP B-restaurant_name

Keyboard NNP I-restaurant_name

Lounge NNP I-restaurant_name



Please VB O

book NN O

me PRP O

a DT O

table NN O

at IN O

a DT O

bistro NN B-restaurant_type

which WDT O

serves VBZ O

lorna JJR B-served_dish

doone NN I-served_dish

. . O



I PRP O

want VBP O

to TO O

book NN O

a DT O

restaurant NN B-restaurant_type

for IN O

six CD B-party_size_number

people NNS O

in IN O

Wagstaff NNP B-city

AK NNP B-state

. . O



I PRP O

would MD O

like VB O

to TO O

book NN O

a DT O

highly RB B-sort

rated VBN I-sort

restaurant NN B-restaurant_type

for IN O

a DT 

In [20]:
class Preprocessing():
    def __init__(self):
        
    

SyntaxError: unexpected EOF while parsing (<ipython-input-20-550feeb00ae2>, line 4)